In [5]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [6]:
import os
BASE_PATH = os.path.join('drive', 'My Drive', '모비컴 2021')
DATA_PATH = os.path.join(BASE_PATH, 'cafedata')
# NOTEBOOKS_PATH = os.path.join(BASE_PATH, 'Notes')
print(os.listdir(BASE_PATH))
print(os.listdir(DATA_PATH))

['Analysis.ipynb', '인터뷰 질문지 supplementary material.gdoc', '취약지역.pdf', '인터뷰 질문지.gdoc', '3 17.gdoc', '3 19.gdoc', 'Team Exercise (03 11).gslides', '3 25.gdoc', '3 31 - 이영기 교수님 미팅.gdoc', '210319_미팅.gdoc', '4 8_문진 로직 문의.gdoc', '산전관리 데이터 수집 관리 어플리케이션 개요.gdoc', '의사선생님들이 들려주시는 각종 산부인과 의학상식.gdoc', '4 16.gdoc', '외래 간호사 인터뷰.gdoc', '4 23.gdoc', '210427 Paper Review_Student Life_Team4.pptx', '210427 Paper Review_Student Life_Team4.pdf', '외래 진찰 참관 속기록.gsheet', 'Proposal Draft.gslides', 'Project Schedule.gsheet', 'mobicom figure.pptx', '챗봇 알러뷰봇 동작 안내.gdoc', '5 14.gdoc', 'Lecture   Paper Presentation List.gsheet', '사용 시나리오.gdoc', 'cafe.gsheet', 'cafedata', 'cafedata_unified.json', 'Midterm Presentation Draft.gslides', '카페 분석.gsheet', 'Final Presentation.gslides']
['P5_55566357.json', 'P5_55558112.json', 'P5_55543623.json', 'P5_55539035.jso

In [7]:
filenames = [i for i in os.listdir(DATA_PATH) if i.endswith("json")]
len(filenames)

1233

In [8]:
# import json
# data = []
# for filename in filenames:
#   filepath = os.path.join(DATA_PATH, filename)
#   with open(filepath) as f:
#     data.append(json.loaTd(f))
# len(data)

In [9]:
# save_path = os.path.join(BASE_PATH, "cafedata_unified.json")
# with open(save_path, "w") as f:
#   f.write(json.dumps(data))

In [10]:
import json
save_path = os.path.join(BASE_PATH, "cafedata_unified.json")
data = None
with open(save_path) as f:
  data = json.load(f)
data[0]

{'author': '줌마양이',
 'contents': ['생후 25일이구요,',
  '아이엠마더 조리원서 부터 먹다가 집에오니 배앓이심하고 녹변보길래 압타밀로 바꾼다고 그제부터 시도했어요. 그제 한번 어제 두번 먹이고  변은 황금색으로 잘보던데 오늘 아침에 한번먹고 소화가 잘되서 허기진지 한시간 좀 지나니 배고파하더라구요. 그래서 아이엠마더 먹였는데 또 한시간 반 지나서 달라는 것 같아서 아이엠 마더 먹이는도중에 분수토를 쫙! 이래도 괜찮은 건지 모르겠네요. 이것저것 먹어서 애 소화력에 문제생긴건지 ㅜㅜ 분수토는 첨봐서 당황스러워요.'],
 'date': '2021.05.07. 11:42',
 'id': '55566357',
 'title': '분유갈아탄다고 퐁당퐁당 먹이다가',
 'title_category': '[0ㅡ1개월]'}

In [11]:
sentences = sum([[entry['title'], *entry['contents']] for entry in data], [])
len(sentences), sentences[0]

(8321, '분유갈아탄다고 퐁당퐁당 먹이다가')

In [12]:
!pip install konlpy

     |████████████████████████████████| 19.4MB 214kB/s 
     |████████████████████████████████| 92kB 9.5MB/s 
     |████████████████████████████████| 460kB 41.2MB/s 
  Found existing installation: beautifulsoup4 4.6.3
    Uninstalling beautifulsoup4-4.6.3:
      Successfully uninstalled beautifulsoup4-4.6.3


In [13]:
import logging

from konlpy.tag import Okt

okt = None


def load_tagger():
    global okt
    logging.info('Initializing Okt pos-tagger')
    okt = Okt()
    okt.pos('엔진 초기화용 문장')


class MorphTokenizer:
    def __init__(self):
        self._tagger = None
        self.stoplist = ['것', '적', '한다', '예컨대', '예']
        self.excluded_tags = ['Josa', 'Punctuation', 'Foreign']

    @property
    def tagger(self):
        if self._tagger is None:
            if okt is None:
                load_tagger()
            self._tagger = okt
        return self._tagger

    def tokenize(self, document):
        return [
            f'{word}/{tag}' for word, tag in self.tagger.pos(document)
            if tag not in self.excluded_tags and word not in self.stoplist
        ]

import logging

from gensim import corpora, models, similarities
from gensim.matutils import corpus2dense

class Vectorizer:
    def train(self, corpus):
        pass

    def get_sentence_vector(self, sentence):
        pass

    def get_sentence_vectors(self, sentences):
        return [
            self.get_sentence_vector(sentence)
            for sentence in sentences
        ]

class LsiVectorizer(Vectorizer):
    def __init__(self):
        logging.info('Start initializing LsiVectorizer...')
        self.dictionary = None
        self.tokenizer = MorphTokenizer()

    def train(self, corpus):
        tokenized_corpus = [
            self.tokenizer.tokenize(document)
            for document in corpus
        ]
        # build dictionary
        self.dictionary = corpora.Dictionary(tokenized_corpus)
        # remove words that appear only once
        self.dictionary.filter_tokens([
            token_id for token_id, doc_freq in self.dictionary.dfs.items()
            if doc_freq == 1
        ])
        # build corpus
        self.corpus = [
            self.dictionary.doc2bow(tokenized_document)
            for tokenized_document in tokenized_corpus
        ]
        self.model_tfidf = models.TfidfModel(self.corpus)
        self.corpus_tfidf = self.model_tfidf[self.corpus]
        self.model_lsi = models.LsiModel(
            self.corpus_tfidf, id2word=self.dictionary, num_topics=250
        )
        self.num_topics, num_features = self.model_lsi.get_topics().shape
        logging.info(f'LSI num_topics: {self.num_topics}')
        # └> min(num_topics=250, num_documents)
        self.corpus_lsi = self.model_lsi[self.corpus_tfidf]
        self.index_lsi = similarities.MatrixSimilarity(
            self.corpus_lsi, num_features=num_features)
        # └> self.index_lsi[lsi_vector] => similarities to each document

    def get_sentence_vector(self, sentence):
        tokenized_sentence = self.tokenizer.tokenize(sentence)
        # └> ['못/Noun', '찾겠다/Verb', '이번/Noun', ... ]
        bow_sentence = self.dictionary.doc2bow(tokenized_sentence)
        # └> [(112, 1), (178, 1), (284, 1), (471, 1), ... ]
        tfidf_vector = self.model_tfidf[bow_sentence]
        # └> : [(112, 0.19214051340327296), (178, 0.23739237055277979), ... ]
        lsi_vector = self.model_lsi[tfidf_vector]
        # └> : [(0, 0.021546872908136172), (1, 0.004916200019640246), ... ]
        # └> : length = self.num_topics
        dense_vector = corpus2dense([lsi_vector], self.num_topics)[:, 0]
        return dense_vector

In [14]:
vectorizer = LsiVectorizer()
vectorizer.train(sentences)

In [15]:
vectorizer.model_lsi.print_topics(-1)

[(0,
  '0.401*"ㅠㅠ/KoreanParticle" + 0.274*"주/Noun" + 0.249*"요/Noun" + 0.171*"배/Noun" + 0.160*"오늘/Noun" + 0.159*"아기/Noun" + 0.153*"너무/Adverb" + 0.143*"안/VerbPrefix" + 0.125*"임신/Noun" + 0.119*"다/Adverb"'),
 (1,
  '-0.587*"ㅠㅠ/KoreanParticle" + 0.573*"주/Noun" + 0.185*"오늘/Noun" + 0.160*"3일/Number" + 0.135*"2/Number" + 0.129*"차/Noun" + -0.108*"너무/Adverb" + 0.096*"검사/Noun" + 0.092*"4일/Number" + 0.092*"냉동/Noun"'),
 (2,
  '-0.546*"ㅠㅠ/KoreanParticle" + 0.494*"요/Noun" + -0.322*"주/Noun" + 0.163*"될까/Verb" + 0.123*"아기/Noun" + -0.116*"배/Noun" + 0.113*"안/VerbPrefix" + 0.109*"할까/Verb" + 0.102*"저/Noun" + -0.101*"오늘/Noun"'),
 (3,
  '-0.710*"배/Noun" + 0.339*"ㅠㅠ/KoreanParticle" + 0.287*"요/Noun" + -0.162*"너무/Adverb" + -0.144*"아랫/Modifier" + -0.141*"느낌/Noun" + 0.133*"주/Noun" + -0.128*"통증/Noun" + -0.109*"좀/Noun" + -0.101*"뭉침/Verb"'),
 (4,
  '-0.549*"요/Noun" + -0.390*"배/Noun" + 0.298*"아기/Noun" + 0.190*"너무/Adverb" + -0.181*"될까/Verb" + 0.180*"다/Adverb" + 0.157*"들/Verb" + -0.156*"주/Noun" + 0.146*"들/Suffix" + 0.12

In [16]:
# from sklearn.feature_extraction.text import TfidfVectorizer
# vectorizer = TfidfVectorizer()
# X = vectorizer.fit_transform(sentences)
# print(vectorizer.get_feature_names())

In [17]:
tokenized_sentences = [
    vectorizer.tokenizer.tokenize(document)
    for document in sentences
]

In [18]:
tokenized_sentences[0]

['분유/Noun', '갈아탄다고/Verb', '퐁당퐁당/Adverb', '먹이다가/Verb']

In [19]:
from collections import Counter
cnt = Counter(sum(tokenized_sentences, []))

In [20]:
l = []
for tid, token in vectorizer.dictionary.id2token.items():
  tflike = cnt[token]
  idf = vectorizer.model_tfidf.idfs[tid]
  l.append((token, tflike / idf))

l.sort(key=lambda x:-x[1])
l[:200]

[('ㅠㅠ/KoreanParticle', 141.28820422026342),
 ('요/Noun', 98.9166155099829),
 ('주/Noun', 94.36705918894089),
 ('아기/Noun', 63.34715336436409),
 ('안/VerbPrefix', 62.33065748315698),
 ('오늘/Noun', 55.04055934292189),
 ('배/Noun', 49.8220841858372),
 ('때/Noun', 48.592407601612784),
 ('다/Adverb', 46.054971404903355),
 ('너무/Adverb', 45.65740182869165),
 ('병원/Noun', 41.63294832871842),
 ('임신/Noun', 40.104641808976204),
 ('들/Suffix', 38.88536483790267),
 ('정도/Noun', 34.55186707422298),
 ('제/Noun', 34.02379645662998),
 ('좀/Noun', 32.29438958298602),
 ('출산/Noun', 31.5975889304001),
 ('잘/Verb', 29.692753832606165),
 ('이/Determiner', 28.152953993975476),
 ('지금/Noun', 27.321373564428672),
 ('ㅠ/KoreanParticle', 26.52913909185746),
 ('더/Noun', 26.18682761970446),
 ('집/Noun', 24.84700618372516),
 ('2/Number', 24.265015289392625),
 ('하는데/Verb', 24.13738653220864),
 ('한/Determiner', 23.799440110953185),
 ('전/Noun', 23.42007830682976),
 ('저/Noun', 23.41862754973713),
 ('후/Noun', 23.336039591471604),
 ('ㅜㅜ/Ko

In [21]:
vectorizer.get_sentence_vector(sentences[2])

/usr/local/lib/python3.7/dist-packages/gensim/matutils.py:502: FutureWarning: arrays to stack must be passed as a "sequence" type such as list or tuple. Support for non-sequence iterables such as generators is deprecated as of NumPy 1.16 and will raise an error in the future.
  result = np.column_stack(sparse2full(doc, num_terms) for doc in corpus)


array([ 1.30970970e-01,  2.96104536e-03,  3.62629779e-02, -4.35365923e-02,
        6.11659177e-02, -2.48627597e-03,  3.53622288e-02, -2.20412333e-02,
       -9.17971227e-03, -6.25171736e-02, -3.30940522e-02,  5.37218116e-02,
       -6.93282485e-02,  3.81624326e-03,  3.12817022e-02,  6.51363358e-02,
       -1.04699191e-02,  2.79921833e-02,  1.14228182e-01, -1.57283619e-03,
        1.69029925e-04,  4.35454287e-02,  4.81596328e-02,  8.83303508e-02,
        2.63434835e-02,  3.18764411e-02,  4.96600643e-02, -4.84634284e-03,
        2.94371452e-02,  2.09944509e-02, -3.00934631e-02, -1.39693394e-02,
       -1.47934956e-02, -1.82272624e-02, -3.99986617e-02,  7.59817194e-03,
       -7.17658326e-02,  1.75904781e-02,  4.84624356e-02,  4.69913334e-03,
       -3.66476662e-02,  3.43770087e-02, -7.18142185e-03, -6.29380494e-02,
       -1.80295184e-02,  2.20761467e-02,  7.29548708e-02, -1.67682171e-02,
        1.20536601e-02, -5.86554371e-02,  7.26834964e-03,  8.53776559e-03,
       -1.40927965e-02,  

In [22]:
vectorizer.get_sentence_vector("근데 오늘 아침에하고 완전 바로확인하니 한줄이길래 미련없이 화장대위에 올려놓고 2-3시간뒤에 보니 흐릿하게나온것같은데..")

/usr/local/lib/python3.7/dist-packages/gensim/matutils.py:502: FutureWarning: arrays to stack must be passed as a "sequence" type such as list or tuple. Support for non-sequence iterables such as generators is deprecated as of NumPy 1.16 and will raise an error in the future.
  result = np.column_stack(sparse2full(doc, num_terms) for doc in corpus)


array([ 0.09053447,  0.03395845, -0.00524479, -0.03963777,  0.03546594,
        0.00859752,  0.03331356, -0.04127761, -0.01368733, -0.15887284,
       -0.01671915,  0.03707366, -0.05390452, -0.06387333, -0.02222077,
       -0.04125026,  0.00638882,  0.01373412,  0.02058758,  0.0012753 ,
        0.00091931, -0.01023839,  0.0006101 ,  0.01161521, -0.01110064,
        0.00330934,  0.00576731,  0.00478422, -0.01553591,  0.00982968,
        0.00746776, -0.01152767,  0.02288008,  0.00429005, -0.0051113 ,
        0.01080115,  0.00460335,  0.01876005,  0.01329635,  0.0039548 ,
       -0.00340005,  0.00502497, -0.00065702, -0.00237767, -0.01792807,
        0.01111605,  0.01380252,  0.00714025,  0.00125339, -0.02631159,
       -0.02071701,  0.007609  ,  0.00769306,  0.01795928,  0.02487669,
       -0.05235852, -0.07330442,  0.01804267, -0.00570081,  0.03175833,
       -0.04468537,  0.05973664, -0.02721808,  0.00628181, -0.0150416 ,
       -0.00025844, -0.04093152,  0.03170503,  0.03485639, -0.00

In [56]:
from sklearn import svm
import numpy as np
import pandas as pd
import math

In [57]:
# 23 svms
svm_models = [svm.SVC(kernel='linear') for i in range(0, 23)]

In [58]:
xlfile = [i for i in os.listdir(DATA_PATH) if i.endswith("xlsx")][0]
print(xlfile)

p8data.xlsx


In [59]:
p8_data = pd.read_excel(os.path.join(DATA_PATH, xlfile), sheet_name='Sheet1', header=0, usecols="A:X")

In [60]:
p8_data

문장  증상: 질분비물  ...  감정:불쾌   질문
0                    (천식관련)호흡기내과 꼭 대학병원급 가야할까요?? (+추가)       NaN  ...    NaN  1.0
1                               비염이 있는데 임신하고 비염이 심해지더니       NaN  ...    NaN  NaN
2                    잠을 잘 못자니까 컨디션이 떨어지는 날은 천식증상이 올라와요       NaN  ...    NaN  NaN
3                    (가슴 답답함-숨을 못쉴정돈 아니구 답답한정도?, 쌕쌕거림)       NaN  ...    NaN  NaN
4    매일 그런게 아니라 그런지 따신거 마니 마시구 보통 하루이틀 잠 좀 잘자구 쉬면 또...       NaN  ...    NaN  NaN
..                                                 ...       ...  ...    ...  ...
980                                  이러면.. 더내려오면 어떨지 ㅜ       NaN  ...    NaN  NaN
981  이러다가 강도도세지구 규칙적으로 변하다가 진진통이 오는거죠..? 어차피 올거면 빨리...       NaN  ...    NaN  1.0
982             진통 체크할때 종료 누르는 시점은 통증이 아예 사라지면 누르나요..?       NaN  ...    NaN  1.0
983                                어쩔땐 아팟다가 사라졋다 하기도하구       NaN  ...    NaN  NaN
984               어쩔땐 그냥 심하게.아팟다가 조금 덜 아팟다가 이럴때두 잇는데ㅎㅎ       NaN  ...    NaN  NaN

[985 rows x 24 columns]

In [67]:
raw_X = p8_data.iloc[:, 0]
X = raw_X.apply(vectorizer.get_sentence_vector).to_list()

/usr/local/lib/python3.7/dist-packages/gensim/matutils.py:502: FutureWarning: arrays to stack must be passed as a "sequence" type such as list or tuple. Support for non-sequence iterables such as generators is deprecated as of NumPy 1.16 and will raise an error in the future.
  result = np.column_stack(sparse2full(doc, num_terms) for doc in corpus)


[array([ 0.07291476, -0.00981075,  0.1292593 ,  0.06608422, -0.11948269,
        -0.00985364, -0.00145207, -0.01849672,  0.00274464, -0.00535026,
         0.02771194, -0.02263058, -0.00220022,  0.00022046, -0.0099638 ,
         0.00770815, -0.0001569 ,  0.00333932, -0.00884321,  0.00093875,
         0.00164643,  0.00586038,  0.0022408 ,  0.00052351,  0.00266023,
        -0.01418084, -0.01546323, -0.00054824, -0.01191121,  0.00715494,
         0.01659291, -0.01206274, -0.00808581, -0.00241372,  0.01587093,
         0.02051285,  0.01013868, -0.02689478,  0.01046634,  0.00158156,
         0.00059229,  0.02036445, -0.00991038,  0.01253537,  0.00909431,
        -0.0026936 ,  0.00370808,  0.00735692,  0.02298429, -0.0237453 ,
         0.00760327,  0.00580659, -0.01494048, -0.00490247,  0.0045261 ,
         0.01607565, -0.00838404, -0.02490673, -0.01415282,  0.01392662,
        -0.01734177,  0.02529792, -0.02400281, -0.00085317, -0.01976207,
         0.02426837, -0.00847201,  0.02070382,  0.0

In [79]:
valid_models = []
for i, model in enumerate(svm_models) :
  raw_Y = p8_data.iloc[:, i+1]
  y = raw_Y.apply(lambda x: 0 if math.isnan(float(x)) else float(x)).to_list()
  if len(set(y)) > 1 :
    #print(y)
    model.fit(X, y)
    valid_models.append(True)
  else :
    valid_models.append(False)

In [73]:
p19file = [i for i in os.listdir(DATA_PATH) if i.endswith("xlsx")][1]
print(p19file)

p19data.xlsx


In [74]:
p19_data = pd.read_excel(os.path.join(DATA_PATH, p19file), sheet_name='Sheet1', header=0, usecols="A:X")

In [78]:
raw_p = p19_data.iloc[:, 0]
p = raw_p.apply(vectorizer.get_sentence_vector).to_list()


/usr/local/lib/python3.7/dist-packages/gensim/matutils.py:502: FutureWarning: arrays to stack must be passed as a "sequence" type such as list or tuple. Support for non-sequence iterables such as generators is deprecated as of NumPy 1.16 and will raise an error in the future.
  result = np.column_stack(sparse2full(doc, num_terms) for doc in corpus)


[array([ 1.30748570e-01, -1.52479678e-01, -1.06387526e-01,  7.48680383e-02,
         1.82153769e-02, -2.34495406e-03,  5.41184703e-03,  6.81864172e-02,
         9.05453041e-03, -1.51311271e-02,  4.56142752e-03,  2.59480029e-02,
         1.31679373e-02, -9.23024584e-03,  7.03957491e-03,  1.77282795e-01,
        -2.46083941e-02,  9.13266242e-02,  8.70546028e-02, -2.80352752e-03,
        -2.13912316e-03,  1.16810314e-01, -2.17747856e-02, -9.18663442e-02,
        -7.68301859e-02, -1.01293534e-01, -4.94576506e-02,  6.27055243e-02,
        -5.24865510e-03,  1.09973364e-01, -3.00382078e-02, -6.04691766e-02,
        -4.34217565e-02,  2.21842173e-02, -5.74749298e-02,  2.81459894e-02,
        -2.24579126e-02,  6.18872512e-03, -6.10039905e-02, -2.70643294e-01,
         1.53963799e-02,  1.19229190e-01, -1.10506512e-01,  1.05238497e-01,
         2.95086980e-01,  5.28820045e-02,  1.18901178e-01,  5.23625053e-02,
        -8.87740999e-02, -3.26424912e-02,  1.32502541e-01, -2.79392917e-02,
         6.8

In [90]:
column_headers = p19_data.columns.values
column_headers[0]


'문장'

In [116]:
output = {}

In [117]:

for i, model in enumerate(svm_models):
  ckey = column_headers[i+1]
  if valid_models[i] :
    print('valid', key)
    predicted = model.predict(p)
    print(len(predicted))
    output[ckey] = predicted
  else :
    print('not valid', key)
    output[ckey] = [0 for j in range(0, 236)]


valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
not valid 질문
not valid 질문
not valid 질문
not valid 질문
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236
valid 질문
236


In [118]:
output

{'감정:분노': array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
   

In [119]:
df = pd.DataFrame(output)
df

증상: 질분비물  증상:태동감소  증상:자궁수축/복통  증상: 산도/경부길이  ...  감정:행복  감정:슬픔  감정:불쾌   질문
0         0.0      0.0         0.0          0.0  ...    0.0    0.0    0.0  0.0
1         0.0      0.0         0.0          0.0  ...    0.0    0.0    0.0  0.0
2         0.0      0.0         0.0          0.0  ...    0.0    0.0    0.0  0.0
3         0.0      0.0         0.0          0.0  ...    0.0    0.0    0.0  0.0
4         0.0      0.0         0.0          0.0  ...    0.0    0.0    0.0  0.0
..        ...      ...         ...          ...  ...    ...    ...    ...  ...
231       0.0      0.0         1.0          0.0  ...    0.0    0.0    0.0  0.0
232       0.0      0.0         0.0          0.0  ...    0.0    0.0    0.0  0.0
233       0.0      0.0         0.0          0.0  ...    0.0    0.0    0.0  0.0
234       0.0      0.0         0.0          0.0  ...    0.0    0.0    0.0  0.0
235       0.0      0.0         1.0          0.0  ...    0.0    0.0    0.0  0.0

[236 rows x 23 columns]

In [121]:
df.to_excel(os.path.join(DATA_PATH, p19file), sheet_name='Sheet2')